# Walker-Penrose Killing tensor in Kerr spacetime

This worksheet demonstrates a few capabilities of SageMath in computations regarding Kerr spacetime. More precisely, it focuses of the Killing tensor $K$ found by Walker & Penrose [[Commun. Math. Phys. **18**, 265 (1970)](https://doi.org/10.1007/BF01649445)].
The employed differential geometry tools have been developed within the  [SageManifolds](http://sagemanifolds.obspm.fr) project (version 1.2, as included in SageMath 8.2).

Click [here](https://raw.githubusercontent.com/sagemanifolds/SageManifolds/master/Worksheets/v1.2/SM_Kerr_Killing_tensor.ipynb) to download the worksheet file (ipynb format). To run it, you must start SageMath within the Jupyter notebook, via the command `sage -n jupyter`

*NB:* a version of SageMath at least equal to 8.2 is required to run this worksheet:

In [1]:
version()

'SageMath version 8.2, Release Date: 2018-05-05'

First we set up the notebook to display mathematical objects using LaTeX rendering:

In [2]:
%display latex

We also define a viewer for 3D plots (use `'threejs'` or `'jmol'` for interactive 3D graphics):

In [3]:
viewer3D = 'threejs' # must be 'threejs', jmol', 'tachyon' or None (default)

To speed up the computations, we ask for running them in parallel on 8 cores:

In [4]:
Parallelism().set(nproc=8)

## Spacetime manifold

We declare the Kerr spacetime (or more precisely the Boyer-Lindquist domain of Kerr spacetime) as a 4-dimensional Lorentzian manifold:

In [5]:
M = Manifold(4, 'M', latex_name=r'\mathcal{M}', structure='Lorentzian')
print(M)

4-dimensional Lorentzian manifold M


Let us declare the **Boyer-Lindquist coordinates** via the method `chart()`, the argument of which is a string expressing the coordinates names, their ranges (the default is $(-\infty,+\infty)$) and their LaTeX symbols:

In [6]:
BL.<t,r,th,ph> = M.chart(r't r:(0,+oo) th:(0,pi):\theta ph:(0,2*pi):\phi') 
print(BL) ; BL

Chart (M, (t, r, th, ph))


Chart (M, (t, r, th, ph))

In [7]:
BL[0], BL[1]

(t, r)

<h2>Metric tensor</h2>

<p>The 2 parameters $m$ and $a$ of the Kerr spacetime are declared as symbolic variables:</p>

In [8]:
var('m, a', domain='real')

(m, a)

We get the (yet undefined) spacetime metric by 

In [9]:
g = M.metric()

<p>The metric is set by its components in the coordinate frame associated with Boyer-Lindquist coordinates, which is the current manifold's default frame:</p>

In [10]:
rho2 = r^2 + (a*cos(th))^2
Delta = r^2 -2*m*r + a^2
g[0,0] = -(1-2*m*r/rho2)
g[0,3] = -2*a*m*r*sin(th)^2/rho2
g[1,1], g[2,2] = rho2/Delta, rho2
g[3,3] = (r^2+a^2+2*m*r*(a*sin(th))^2/rho2)*sin(th)^2
g.display()

g = (2*m*r/(a^2*cos(th)^2 + r^2) - 1) dt*dt - 2*a*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2) dt*dph + (a^2*cos(th)^2 + r^2)/(a^2 - 2*m*r + r^2) dr*dr + (a^2*cos(th)^2 + r^2) dth*dth - 2*a*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2) dph*dt + (2*a^2*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2) + a^2 + r^2)*sin(th)^2 dph*dph

<p>A matrix view of the components with respect to the manifold's default vector frame:</p>

In [11]:
g[:]

[                                  2*m*r/(a^2*cos(th)^2 + r^2) - 1                                                                 0                                                                 0                          -2*a*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2)]
[                                                                0                         (a^2*cos(th)^2 + r^2)/(a^2 - 2*m*r + r^2)                                                                 0                                                                 0]
[                                                                0                                                                 0                                               a^2*cos(th)^2 + r^2                                                                 0]
[                         -2*a*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2)                                                                 0                                                                 0 (2*a^2*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2) + a^2 + r^2)*sin(th)^2]

<p>The list of the non-vanishing components:</p>

In [12]:
g.display_comp()

g_t,t = 2*m*r/(a^2*cos(th)^2 + r^2) - 1 
g_t,ph = -2*a*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2) 
g_r,r = (a^2*cos(th)^2 + r^2)/(a^2 - 2*m*r + r^2) 
g_th,th = a^2*cos(th)^2 + r^2 
g_ph,t = -2*a*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2) 
g_ph,ph = (2*a^2*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2) + a^2 + r^2)*sin(th)^2

<h2>Levi-Civita Connection</h2>

<p>The Levi-Civita connection $\nabla$ associated with $g$:</p>

In [13]:
nabla = g.connection() ; print(nabla)

Levi-Civita connection nabla_g associated with the Lorentzian metric g on the 4-dimensional Lorentzian manifold M


<p>Let us verify that the covariant derivative of $g$ with respect to $\nabla$ vanishes identically:</p>

In [14]:
nabla(g).display()

nabla_g(g) = 0

<h2>Killing vectors</h2>
<p>The default vector frame on the spacetime manifold is the coordinate basis associated with Boyer-Lindquist coordinates:</p>

In [15]:
M.default_frame() is BL.frame()

True

In [16]:
BL.frame()

Coordinate frame (M, (d/dt,d/dr,d/dth,d/dph))

<p>Let us consider the first vector field of this frame:</p>

In [17]:
xi = BL.frame()[0] ; xi

Vector field d/dt on the 4-dimensional Lorentzian manifold M

In [18]:
print(xi)

Vector field d/dt on the 4-dimensional Lorentzian manifold M


<p>The 1-form associated to it by metric duality is</p>

In [19]:
xi_form = xi.down(g) ; xi_form.display()

-(a^2*cos(th)^2 - 2*m*r + r^2)/(a^2*cos(th)^2 + r^2) dt - 2*a*m*r*sin(th)^2/(a^2*cos(th)^2 + r^2) dph

<p>Its covariant derivative is</p>

In [20]:
nab_xi = nabla(xi_form) ; print(nab_xi) ; nab_xi.display()

Tensor field of type (0,2) on the 4-dimensional Lorentzian manifold M


(a^2*m*cos(th)^2 - m*r^2)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4) dt*dr + 2*a^2*m*r*cos(th)*sin(th)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4) dt*dth - (a^2*m*cos(th)^2 - m*r^2)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4) dr*dt + (a^3*m*cos(th)^2 - a*m*r^2)*sin(th)^2/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4) dr*dph - 2*a^2*m*r*cos(th)*sin(th)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4) dth*dt + 2*(a^3*m*r + a*m*r^3)*cos(th)*sin(th)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4) dth*dph - (a^3*m*cos(th)^2 - a*m*r^2)*sin(th)^2/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4) dph*dr - 2*(a^3*m*r + a*m*r^3)*cos(th)*sin(th)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4) dph*dth

<p>Let us check that the Killing equation is satisfied:</p>

In [21]:
nab_xi.symmetrize() == 0

True

<p>Similarly, let us check that $\frac{\partial}{\partial\phi}$ is a Killing vector:</p>

In [22]:
chi = BL.frame()[3] ; chi

Vector field d/dph on the 4-dimensional Lorentzian manifold M

In [23]:
nabla(chi.down(g)).symmetrize() == 0

True

## Principal null vectors

We introduce the principal null vectors $k$ and $\ell$ of Kerr spacetime:

In [24]:
k = M.vector_field(name='k')
k[:] = [(r^2+a^2)/(2*rho2), -Delta/(2*rho2), 0, a/(2*rho2)]
k.display()

k = 1/2*(a^2 + r^2)/(a^2*cos(th)^2 + r^2) d/dt - 1/2*(a^2 - 2*m*r + r^2)/(a^2*cos(th)^2 + r^2) d/dr + 1/2*a/(a^2*cos(th)^2 + r^2) d/dph

In [25]:
el = M.vector_field(name='el', latex_name=r'\ell')
el[:] = [(r^2+a^2)/Delta, 1, 0, a/Delta]
el.display()

el = (a^2 + r^2)/(a^2 - 2*m*r + r^2) d/dt + d/dr + a/(a^2 - 2*m*r + r^2) d/dph

Let us check that $k$ and $\ell$ are null vectors:

In [26]:
g(k,k).expr()

0

In [27]:
g(el,el).expr()

0

Their scalar product is $-1$:

In [28]:
g(k,el).expr()

-1

Note that the scalar product (with respect to metric $g$) can also be computed by means of the method `dot`:

In [29]:
k.dot(el).expr()

-1

Let us evaluate the "acceleration" of $k$, i.e. $\nabla_k k$:

In [30]:
acc_k = nabla(k).contract(k)
acc_k.display()

1/2*(a^4*m - m*r^4 - (a^4*m - a^4*r + a^2*m*r^2 - a^2*r^3)*sin(th)^2)/(a^6*cos(th)^6 + 3*a^4*r^2*cos(th)^4 + 3*a^2*r^4*cos(th)^2 + r^6) d/dt - 1/2*(a^4*m - 2*a^2*m^2*r + 2*m^2*r^3 - m*r^4 - (a^4*m + 3*a^2*m*r^2 - a^2*r^3 - (a^4 + 2*a^2*m^2)*r)*sin(th)^2)/(a^6*cos(th)^6 + 3*a^4*r^2*cos(th)^4 + 3*a^2*r^4*cos(th)^2 + r^6) d/dr + 1/2*(a^3*m - a*m*r^2 - (a^3*m - a^3*r)*sin(th)^2)/(a^6*cos(th)^6 + 3*a^4*r^2*cos(th)^4 + 3*a^2*r^4*cos(th)^2 + r^6) d/dph

We check that $k$ is a pregeodesic vector, i.e. that $\nabla_k k = \kappa_k k$ for some scalar field $\kappa_k$:

In [31]:
for i in [0,1,3]:
    show(acc_k[i] / k[i])

(a^2*m - m*r^2 - (a^2*m - a^2*r)*sin(th)^2)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4)

(a^2*m - m*r^2 - (a^2*m - a^2*r)*sin(th)^2)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4)

(a^2*m - m*r^2 - (a^2*m - a^2*r)*sin(th)^2)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4)

In [32]:
kappa_k = acc_k[[0]] / k[[0]]
kappa_k.display()

M --> R
(t, r, th, ph) |--> (a^2*m - m*r^2 - (a^2*m - a^2*r)*sin(th)^2)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4)

In [33]:
acc_k == kappa_k * k

True

Similarly let us evaluate the "acceleration" of $\ell$:

In [34]:
acc_l = nabla(el).contract(el)
acc_l.display()

0

Hence $\ell$ is a geodesic vector.

## Walker-Penrose Killing tensor

We need the 1-forms associated to $k$ and $\ell$ by metric duality:

In [35]:
uk = k.down(g)
ul = el.down(g)

The Walker-Penrose Killing tensor $K$ is then formed as
$$ K = \rho^2 (\underline{\ell}\otimes \underline{k} + (\underline{k}\otimes \underline{\ell}) + r^2 g $$

In [36]:
K = rho2*(ul*uk+ uk*ul) + r^2*g
K.set_name('K')
print(K)

Tensor field K of type (0,2) on the 4-dimensional Lorentzian manifold M


In [37]:
K.display_comp()

K_t,t = (a^2*r^2 + (a^4 - 2*a^2*m*r)*cos(th)^2)/(a^2*cos(th)^2 + r^2) 
K_t,ph = -(2*a^3*m*r*sin(th)^4 - (2*a^3*m*r - a^3*r^2 - a*r^4 - (a^5 + a^3*r^2)*cos(th)^2)*sin(th)^2)/(a^2*cos(th)^2 + r^2) 
K_r,r = -(a^4*cos(th)^4 + a^2*r^2*cos(th)^2)/(a^2 - 2*m*r + r^2) 
K_th,th = a^2*r^2*cos(th)^2 + r^4 
K_ph,t = -(2*a^3*m*r*sin(th)^4 - (2*a^3*m*r - a^3*r^2 - a*r^4 - (a^5 + a^3*r^2)*cos(th)^2)*sin(th)^2)/(a^2*cos(th)^2 + r^2) 
K_ph,ph = ((a^8 - 2*a^6*m*r + a^6*r^2)*sin(th)^8 - (2*a^8 - 4*a^6*m*r + 3*a^6*r^2 - 2*a^4*m*r^3 + a^4*r^4)*sin(th)^6 + (a^8 - 2*a^6*m*r + a^6*r^2 - 2*a^4*m*r^3 - a^4*r^4 - a^2*r^6)*sin(th)^4 + (a^6*r^2 + 3*a^4*r^4 + 3*a^2*r^6 + r^8)*sin(th)^2)/(a^4*cos(th)^4 + 2*a^2*r^2*cos(th)^2 + r^4)

In [38]:
DK = nabla(K)
print(DK)

Tensor field nabla_g(K) of type (0,3) on the 4-dimensional Lorentzian manifold M


In [39]:
DK.display_comp()

nabla_g(K)_t,r,ph = a*r*sin(th)^2 
nabla_g(K)_t,th,ph = (a^3 - 2*a*m*r + a*r^2)*cos(th)*sin(th) 
nabla_g(K)_t,ph,r = -a*r*sin(th)^2 
nabla_g(K)_t,ph,th = -(a^3 - 2*a*m*r + a*r^2)*cos(th)*sin(th) 
nabla_g(K)_r,t,ph = -a*r*cos(th)^2 + a*r 
nabla_g(K)_r,r,th = 2*(a^4*cos(th)^3 + a^2*r^2*cos(th))*sin(th)/(a^2 - 2*m*r + r^2) 
nabla_g(K)_r,th,r = -(a^4*cos(th)^3 + a^2*r^2*cos(th))*sin(th)/(a^2 - 2*m*r + r^2) 
nabla_g(K)_r,th,th = -a^2*r*cos(th)^2 - r^3 
nabla_g(K)_r,ph,ph = -a^2*r - r^3 + (a^2*r + r^3)*cos(th)^2 
nabla_g(K)_th,t,ph = (a^3 - 2*a*m*r + a*r^2)*cos(th)*sin(th) 
nabla_g(K)_th,r,r = -(a^4*cos(th)^3 + a^2*r^2*cos(th))*sin(th)/(a^2 - 2*m*r + r^2) 
nabla_g(K)_th,r,th = -a^2*r*cos(th)^2 - r^3 
nabla_g(K)_th,th,r = 2*a^2*r*cos(th)^2 + 2*r^3 
nabla_g(K)_th,ph,ph = -(a^4 - 2*a^2*m*r + a^2*r^2)*cos(th)*sin(th)^3 
nabla_g(K)_ph,t,r = -a*r*sin(th)^2 
nabla_g(K)_ph,t,th = -(a^3 - 2*a*m*r + a*r^2)*cos(th)*sin(th) 
nabla_g(K)_ph,r,ph = -(a^2*r + r^3)*sin(th)^2 
nabla_g(K)_ph,th,ph = -(a^4 - 2*a^2*m*r + a^2*r^2)*cos(th)*sin(th)^3 
nabla_g(K)_ph,ph,r = 2*(a^2*r + r^3)*sin(th)^2 
nabla_g(K)_ph,ph,th = 2*(a^4 - 2*a^2*m*r + a^2*r^2)*cos(th)*sin(th)^3

Let us check that $K$ is a Killing tensor:

In [40]:
DK.symmetrize().display()

0

Equivalently, we may write, using index notation:

In [41]:
DK['_(abc)'].display()

0